In [28]:
"""import bibliotek"""
import gzip

from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS 
from gensim.models import Word2Vec, LdaMulticore

from gensim.corpora import Dictionary

import numpy as np
import pyLDAvis

from pyLDAvis import gensim



In [29]:
# odczyt danych informacje o hotelach i samochodach
# https://github.com/kavgan/OpinRank dane o autoach i hotelach
# http://kavita-ganesan.com/entity-ranking-data/#.Xndm1qhKiUk
with gzip.open('input/data/reviews_data.txt.gz' , 'rb') as f:
    for i , line in enumerate(f):
        print (i, line)
        break

0 b"Oct 12 2009 \tNice trendy hotel location not too bad.\tI stayed in this hotel for one night. As this is a fairly new place some of the taxi drivers did not know where it was and/or did not want to drive there. Once I have eventually arrived at the hotel, I was very pleasantly surprised with the decor of the lobby/ground floor area. It was very stylish and modern. I found the reception's staff geeting me with 'Aloha' a bit out of place, but I guess they are briefed to say that to keep up the coroporate image.As I have a Starwood Preferred Guest member, I was given a small gift upon-check in. It was only a couple of fridge magnets in a gift box, but nevertheless a nice gesture.My room was nice and roomy, there are tea and coffee facilities in each room and you get two complimentary bottles of water plus some toiletries by 'bliss'.The location is not great. It is at the last metro stop and you then need to take a taxi, but if you are not planning on going to see the historic sites in 

In [30]:
"""pomocniczne funckcje"""
#usuwa STOPWORDs
def preprocessing(sentence):
    return [word for word in simple_preprocess(sentence) \
            if word not in STOPWORDS]

#czyta dane z pliku
def read_sencences (filename):
    with gzip.open(filename, 'rb') as f:
        for line in f:
            yield preprocessing(line)

In [51]:
#wczytanie danych z pliku
sentences = read_sencences('input/data/reviews_data.txt.gz')

In [58]:
#pokazuje kolejne zdania ze zbioru sentences
next (sentences)

['jul',
 'stylish',
 'clean',
 'reasonable',
 'value',
 'poor',
 'location',
 'glad',
 'person',
 'post',
 'photos',
 'hotel',
 'key',
 'points',
 'property',
 'starwood',
 'property',
 'cheaper',
 'rest',
 'shows',
 'pretty',
 'incompetent',
 'reception',
 'staff',
 'hard',
 'bed',
 'cheap',
 'blinds',
 'block',
 'sun',
 'mornings',
 'common',
 'areas',
 'degrading',
 'quickly',
 'given',
 'new',
 'hotel',
 'clean',
 'tidy',
 'important',
 'hotel',
 'presents',
 'good',
 'value',
 'stylishly',
 'designed',
 'looks',
 'modern',
 'price',
 'range',
 'location',
 'poor',
 'typical',
 'tourist',
 'yes',
 'poor',
 'close',
 'cheaper',
 'summer',
 'palace',
 'places',
 'require',
 'taxi',
 'probably',
 'result',
 'hours',
 'frustratingly',
 'stuck',
 'traffic',
 'taxi',
 'drivers',
 'dont',
 'know',
 'coming',
 'east',
 'city',
 'centre',
 'airport',
 'right',
 'turn',
 'points',
 'hotel',
 'adjacent',
 'trying',
 'scam',
 'spg',
 'platinum',
 'status',
 'cheapest',
 'way',
 'possible',
 's

In [59]:
#jak dlugo wykonuje funkcje
%time  sentences = list(read_sencences('input/data/reviews_data.txt.gz'))

Wall time: 2min 7s


In [60]:
#ile zdan wczytano
len (sentences)

255404

In [61]:
#przyklad jak dziala simple_preprocess
#zamienia na male litery, usuwa zbyt ktróki zbyt długie słowa, dzieli zdanie na słowa
simple_preprocess('tGood value but not downtown\tThis hotel is located next to the Four Points Hotel and are both part of the Starw')

['tgood',
 'value',
 'but',
 'not',
 'downtown',
 'this',
 'hotel',
 'is',
 'located',
 'next',
 'to',
 'the',
 'four',
 'points',
 'hotel',
 'and',
 'are',
 'both',
 'part',
 'of',
 'the',
 'starw']

In [62]:
#przyklad jak dziala STOPWORDS
#usuwa STOPWORDS
sentene = 'tGood value but not downtown\tThis hotel is located next to the Four Points Hotel and are both part of the Starw'
[word for word in simple_preprocess(sentene) if word not in STOPWORDS]

['tgood', 'value', 'downtown', 'hotel', 'located', 'points', 'hotel', 'starw']

## MODEL

In [63]:
#trenowanie modelu
#% time model = Word2Vec(sentences, size = 100, window = 5 , min_count =2)

#wczytanie gotowego modelu
model = Word2Vec.load('input/models/hotel_model_size300_window10_mincount2.model')

## Reprezentacja wektorowa

In [64]:
#podobne do good, bad
model.wv.most_similar('good')
model.wv.most_similar('bad')


[('terrible', 0.612427830696106),
 ('horrible', 0.5884307026863098),
 ('awful', 0.5449715852737427),
 ('crappy', 0.49739760160446167),
 ('complain', 0.48276573419570923),
 ('horrid', 0.4751036763191223),
 ('horrendous', 0.47043710947036743),
 ('lousy', 0.46792906522750854),
 ('worse', 0.4651168882846832),
 ('nasty', 0.46399790048599243)]

In [65]:
model.wv.most_similar('bmw')


[('mercedes', 0.7925524115562439),
 ('audi', 0.7878206968307495),
 ('maybach', 0.7843899726867676),
 ('chauffeur', 0.7694282531738281),
 ('customs', 0.750923752784729),
 ('chauffer', 0.7457523941993713),
 ('limousine', 0.7409721612930298),
 ('driven', 0.7043405771255493),
 ('benz', 0.6980505585670471),
 ('immigration', 0.6966387033462524)]

In [66]:
model.wv.most_similar(positive = ['bad','horrible'], negative = ['good'])

[('terrible', 0.6980762481689453),
 ('awful', 0.6874771118164062),
 ('nasty', 0.59563148021698),
 ('horrid', 0.5912722945213318),
 ('crappy', 0.5864940285682678),
 ('horrific', 0.5861026644706726),
 ('disgusting', 0.581505298614502),
 ('worst', 0.5805123448371887),
 ('ugh', 0.5666265487670898),
 ('nightmare', 0.5568656921386719)]

## Topic modeling - LDA

In [67]:
#wymieszanie zdan ze zbioru wejsciowego aby nie bylo zaleznosci
sentences_light = np.random.permutation(sentences)

In [68]:
#bierzemy 10000 zdan do zbioru
sentences_light = sentences_light[:10000]

In [69]:
#tworzy slownik z unikalnymi slowami
%time dictionary = Dictionary(sentences_light)

Wall time: 2.02 s


In [70]:
list (dictionary.items())#poakzuje id dla unikalnego slowa np 0, 'amazing' itd...

[(0, 'amazing'),
 (1, 'apr'),
 (2, 'ate'),
 (3, 'classic'),
 (4, 'cooked'),
 (5, 'dinner'),
 (6, 'exciting'),
 (7, 'flavorwith'),
 (8, 'history'),
 (9, 'hotel'),
 (10, 'lacking'),
 (11, 'lifetime'),
 (12, 'lot'),
 (13, 'money'),
 (14, 'new'),
 (15, 'nice'),
 (16, 'old'),
 (17, 'overpriced'),
 (18, 'places'),
 (19, 'poorly'),
 (20, 'rooms'),
 (21, 'said'),
 (22, 'special'),
 (23, 'stay'),
 (24, 'steak'),
 (25, 'steakhouse'),
 (26, 'think'),
 (27, 'waldorf'),
 (28, 'york'),
 (29, 'jan'),
 (30, 'klein'),
 (31, 'lage'),
 (32, 'sauber'),
 (33, 'super'),
 (34, 'bed'),
 (35, 'breakfast'),
 (36, 'clean'),
 (37, 'close'),
 (38, 'comfortable'),
 (39, 'concerned'),
 (40, 'continental'),
 (41, 'entered'),
 (42, 'excellent'),
 (43, 'food'),
 (44, 'friend'),
 (45, 'getting'),
 (46, 'great'),
 (47, 'hard'),
 (48, 'head'),
 (49, 'hesitate'),
 (50, 'husband'),
 (51, 'interesting'),
 (52, 'litte'),
 (53, 'little'),
 (54, 'location'),
 (55, 'london'),
 (56, 'long'),
 (57, 'low'),
 (58, 'mades'),
 (59, 'm

In [71]:
len (dictionary)#ilosc w slowniku unikalnych slow

28477

In [72]:
#zlicza ilosc slow w zdaniu wg ponizszego przykladu
%time bow_corpus = [dictionary.doc2bow(sent) for sent in sentences_light ]

Wall time: 1.09 s


In [78]:
#zlicza ile razy wystapilo id slowa w zdaniu
#car (id = 736) 2 raz, hotel (id = 40) 1 raz
dictionary.doc2bow(#['car', 'car', 'hotel'],
                   #['kot','car'],
                   ['car', 'hotel','dog']) 


[(9, 1), (591, 1), (6524, 1)]

In [76]:
#poakzuje id slowa w dictionay
dictionary.token2id[ 'car']

591

In [75]:
bow_corpus

[[(0, 1),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 1),
  (23, 2),
  (24, 1),
  (25, 1),
  (26, 1),
  (27, 1),
  (28, 1)],
 [(29, 1), (30, 1), (31, 1), (32, 1), (33, 3)],
 [(0, 1),
  (9, 3),
  (23, 4),
  (34, 1),
  (35, 2),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 1),
  (41, 1),
  (42, 2),
  (43, 1),
  (44, 1),
  (45, 1),
  (46, 3),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 1),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 1),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 2),
  (63, 1),
  (64, 1),
  (65, 1),
  (66, 3),
  (67, 1),
  (68, 1),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 2),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 1)],
 [(9, 3),
  (29, 1),
  (36, 1),
  (42, 1),
  (43, 2),
  (54, 1),
  (66, 5),
  (72, 1),
  (79, 1),
  (80, 1),
  (81,

In [79]:
# model LDA
# bow_corpus
# dictionary
# num_topics - ilosc tematow
# passes - ile iteracji
%time lda_model = LdaMulticore(bow_corpus, id2word= dictionary, num_topics = 100, passes = 20)

Wall time: 7min 29s


In [80]:
#pokazuje top tematy po wytrenowanieu modelu LDA
for idx , topic in lda_model.print_topics(-1):
    print ('Topic: {} \nWords : {} '.format( idx,topic) )

Topic: 0 
Words : 0.027*"room" + 0.015*"hotel" + 0.013*"night" + 0.010*"view" + 0.009*"stay" + 0.009*"good" + 0.009*"like" + 0.007*"bed" + 0.006*"rooms" + 0.005*"bathroom" 
Topic: 1 
Words : 0.014*"rooms" + 0.010*"good" + 0.010*"great" + 0.008*"staff" + 0.007*"hotel" + 0.007*"food" + 0.006*"small" + 0.006*"room" + 0.006*"location" + 0.005*"stay" 
Topic: 2 
Words : 0.015*"room" + 0.012*"stay" + 0.011*"hooters" + 0.010*"pool" + 0.008*"great" + 0.008*"resort" + 0.006*"stayed" + 0.006*"good" + 0.006*"time" + 0.005*"service" 
Topic: 3 
Words : 0.016*"great" + 0.014*"desert" + 0.011*"place" + 0.010*"hotel" + 0.010*"resort" + 0.008*"room" + 0.008*"pool" + 0.007*"nice" + 0.007*"time" + 0.007*"rose" 
Topic: 4 
Words : 0.021*"hotel" + 0.013*"soho" + 0.013*"quot" + 0.013*"service" + 0.011*"stay" + 0.009*"room" + 0.009*"rooms" + 0.009*"great" + 0.008*"good" + 0.008*"stayed" 
Topic: 5 
Words : 0.039*"room" + 0.025*"hotel" + 0.021*"good" + 0.017*"breakfast" + 0.014*"small" + 0.014*"clean" + 0.011*"l

## Wizualizacja tematów

In [81]:
lda_vis = pyLDAvis.gensim.prepare(lda_model,bow_corpus,dictionary)
pyLDAvis.display(lda_vis)

C:\Users\tskrzypczak\AppData\Local\Continuum\anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


## LDA - wolne długo sie liczy, nie odporne na literowki - np. odmiany w jezyku polskim